# Install

In [ ]:
pip install googlemaps
pip install folium

# 공통 

In [ ]:
with open("../secret_key.json") as f: # path 
    secrets = json.loads(f.read())
    
google_api_key = secrets['google_api_key']

In [2]:
import requests
import folium

def get_coordinates(api_key, address):
    # 구글 맵 API를 통한 주소 검색
    url = f"https://maps.googleapis.com/maps/api/geocode/json?address={address}&key={api_key}"
    response = requests.get(url)
    data = response.json()

    # 결과가 있는 경우 위도와 경도 반환
    if data['status'] == 'OK':
        location = data['results'][0]['geometry']['location']
        lat, lng = location['lat'], location['lng']
        return lat, lng
    else:
        print(f"Failed to get coordinates for address: {address}")
        return None, None

# 구글 맵 API 키 입력


# 지도 생성
map = folium.Map(location=[37.5502, 126.982], zoom_start=12)

# 병원 

In [6]:
import pandas as pd

# 서울시 병원, 의원 data 가져오기
hospital = pd.read_csv('../data/[필수활용01]서울시_병원정보.csv', encoding='cp949') # path 변경해야함
clinic = pd.read_csv('../data/[필수활용02]서울시_의원정보.csv', encoding='cp949', low_memory=False)
print(hospital.columns, '\n')
print(clinic.columns) # '시도', '소재지시도' column 없음

# 병원 종류 살펴보기
print(hospital['의료기관종별명'].value_counts(), '\n')

# 진료과목 null값 확인
print("진료과목내용명 null 개수:", hospital['진료과목내용명'].isnull().sum(), '\n')

# 소아청소년과 병원 영업 상태 확인
pediatrics_hospital = hospital[(hospital['의료기관종별명'].isin(['병원', '한방병원', '종합병원'])) & (hospital['진료과목내용명'].str.contains('소아청소년과'))]
print(pediatrics_hospital['상세영업상태명'].value_counts(), '\n')

# 영업중인 소아청소년과 병원 정보만 남기기
pediatrics_hospital = pediatrics_hospital[pediatrics_hospital['상세영업상태명'] == '영업중']

Index(['번호', '개방서비스명', '개방서비스아이디', '개방자치단체코드', '관리번호', '인허가일자', '인허가취소일자',
       '영업상태구분코드', '영업상태명', '상세영업상태코드', '상세영업상태명', '폐업일자', '휴업시작일자', '휴업종료일자',
       '재개업일자', '소재지전화', '소재지면적', '소재지우편번호', '소재지전체주소', '도로명전체주소', '도로명우편번호',
       '사업장명', '최종수정시점', '데이터갱신구분', '데이터갱신일자', '업태구분명', '좌표정보(x)', '좌표정보(y)',
       '의료기관종별명', '의료인수', '입원실수', '병상수', '총면적', '진료과목내용', '진료과목내용명', '지정취소일자',
       '완화의료지정형태', '완화의료담당부서명', '구급차특수', '구급차일반', '총인원', '구조사수', '허가병상수',
       '최초지정일자', '시도', '도로명시도', '소재지시도'],
      dtype='object') 

Index(['번호', '개방서비스명', '개방서비스아이디', '개방자치단체코드', '관리번호', '인허가일자', '인허가취소일자',
       '영업상태구분코드', '영업상태명', '상세영업상태코드', '상세영업상태명', '폐업일자', '휴업시작일자', '휴업종료일자',
       '재개업일자', '소재지전화', '소재지면적', '소재지우편번호', '소재지전체주소', '도로명전체주소', '도로명우편번호',
       '사업장명', '최종수정시점', '데이터갱신구분', '데이터갱신일자', '업태구분명', '좌표정보(x)', '좌표정보(y)',
       '의료기관종별명', '의료인수', '입원실수', '병상수', '총면적', '진료과목내용', '진료과목내용명', '지정취소일자',
       '완화의료지정형태', '완화의료담당부서명', '구급차특수', '구급차일반', '총인원', '구조사수', '허가병상수',
       '

In [7]:
pediatrics_hospital.columns

Index(['번호', '개방서비스명', '개방서비스아이디', '개방자치단체코드', '관리번호', '인허가일자', '인허가취소일자',
       '영업상태구분코드', '영업상태명', '상세영업상태코드', '상세영업상태명', '폐업일자', '휴업시작일자', '휴업종료일자',
       '재개업일자', '소재지전화', '소재지면적', '소재지우편번호', '소재지전체주소', '도로명전체주소', '도로명우편번호',
       '사업장명', '최종수정시점', '데이터갱신구분', '데이터갱신일자', '업태구분명', '좌표정보(x)', '좌표정보(y)',
       '의료기관종별명', '의료인수', '입원실수', '병상수', '총면적', '진료과목내용', '진료과목내용명', '지정취소일자',
       '완화의료지정형태', '완화의료담당부서명', '구급차특수', '구급차일반', '총인원', '구조사수', '허가병상수',
       '최초지정일자', '시도', '도로명시도', '소재지시도'],
      dtype='object')

In [8]:
# 주소 목록을 순회하면서 위도와 경도를 구하고 지도에 마커 추가
for i in pediatrics_hospital.index:
    address = pediatrics_hospital['도로명전체주소'][i]
    lat, lng = get_coordinates(google_api_key, address)
    if lat is not None and lng is not None:
        folium.Marker([lat, lng], popup=folium.Popup(pediatrics_hospital['사업장명'][i], max_width=300)).add_to(map)
        
# 지도 표시
map

# 의원 

In [9]:
# 의원 종류 살펴보기
print(clinic['의료기관종별명'].value_counts(), '\n')

# 진료과목 null값 확인
print("진료과목내용명 null 개수:", clinic['진료과목내용명'].isnull().sum(), '\n')

# 진료과목 null값 실제로 보기
print(clinic[clinic['진료과목내용명'].isna()][['상세영업상태명', '사업장명']], '\n')

# 진료과목 null값 포함한 행 제거
clinic = clinic.drop(clinic[clinic['진료과목내용명'].isna()].index)
print(clinic['의료기관종별명'].value_counts(), '\n') # 보건소 -1, 조산원 -4

# 소아청소년과 의원 영업 상태 확인
pediatrics_clinic = clinic[clinic['진료과목내용명'].str.contains('소아청소년과')]
print(pediatrics_clinic['상세영업상태명'].value_counts(), '\n')

# 영업중인 소아청소년과 의원 정보만 남기기
pediatrics_clinic = pediatrics_clinic[pediatrics_clinic['상세영업상태명'] == '영업중']

의원      14338
치과의원     7019
한의원      6036
보건소        25
보건지소       12
조산원         9
Name: 의료기관종별명, dtype: int64 

진료과목내용명 null 개수: 5 

      상세영업상태명    사업장명
7973      영업중  구로구보건소
11196     영업중  마마스조산원
11234     영업중   둥지조산원
19367      폐업   호움조산원
24656      폐업  김삼순조산원 

의원      14338
치과의원     7019
한의원      6036
보건소        24
보건지소       12
조산원         5
Name: 의료기관종별명, dtype: int64 

영업중     3052
폐업      1174
직권폐업       3
휴업         3
Name: 상세영업상태명, dtype: int64 



In [11]:
# 병원 
for i in pediatrics_hospital.index:
    address = pediatrics_hospital['도로명전체주소'][i]
    lat, lng = get_coordinates(google_api_key, address)
    if lat is not None and lng is not None:
        folium.Marker([
            lat, lng], 
            popup=folium.Popup(pediatrics_hospital['사업장명'][i], max_width=300)
        ).add_to(map)

# 의원
for i in pediatrics_clinic.index:
    address = pediatrics_clinic['도로명전체주소'][i]
    lat, lng = get_coordinates(google_api_key, address)
    if lat is not None and lng is not None:
        folium.Marker(
            [lat, lng],
            popup=folium.Popup(pediatrics_clinic['사업장명'][i], max_width=300), 
            icon=folium.Icon(color='red')
        ).add_to(map)
        
# 지도 표시
map

Failed to get coordinates for address: 서울특별시 마포구 마포대로24길 4, 공덕자이아파트 상가 304~305호 (아현동)
Failed to get coordinates for address: 서울특별시 서대문구 수색로 100, 103동 6호 (북가좌동, DMC래미안e편한세상)
Failed to get coordinates for address: 서울특별시 서초구 고무래로 32, 203호 (반포동, 반포메딕스빌딩)
Failed to get coordinates for address: 서울특별시 양천구 신정로7길 60-5 (신정동, 동일프라자)


In [14]:
map.save('map_with_markers.html')